In [1]:
import os
import numpy as np
import pandas as pd
from IPython.display import display
from IPython.core.display import HTML
from bokeh.io import output_notebook, show
from bokeh.plotting import figure
from bokeh.models import Div
from bokeh.layouts import row

output_notebook()
pd.options.display.float_format = '{:,.5f}'.format
HTML('<link rel="stylesheet" href="https://maxcdn.bootstrapcdn.com/font-awesome/4.7.0/css/font-awesome.min.css">')

Loading BokehJS ...

Backtesting of the proposal 11487
---

In [2]:
from terra_algo_backtest.binance_loader import new_binance_client

# Replace these with your Binance API key and secret
client = new_binance_client(os.getenv("BINANCE_API_KEY"), os.getenv("BINANCE_API_SECRET"))

In [3]:
from binance import Client
from terra_algo_backtest.utils import format_df
from terra_algo_backtest.plotting import new_trade_figure, plot_price_ratio

mkt_pair = 'USTC/BUSD'
start, end = '2023-01-01 00:00:00', '2023-06-30 23:59:59'
frequency = Client.KLINE_INTERVAL_1HOUR

qty_factor = 0.01
df_trades = client.get_trade_data(mkt_pair, frequency, start, end)
df_trades["quantity"] = qty_factor*df_trades["quantity"]
show(Div(text=format_df(df_trades.head(10), width=800)))

In [4]:
from terra_algo_backtest.market import MarketQuote, new_market
from terra_algo_backtest.simulation import swap_simulation
from terra_algo_backtest.plotting import new_div_simulation_figure
from terra_algo_backtest.exec_engine import ConstantProductEngine
from terra_algo_backtest.strategy import SimpleUniV2Strategy, DivProtocolStrategy

liquidity_usd = 1000000
# USTC/BUSD market price
base = MarketQuote("USTC/BUSD", df_trades.price.iloc[0])
# BUSD/USD market price
quote = MarketQuote("BUSD/USD", 1)
# create a 1,000,000 USD market for USTC/BUSD with 0.3% swap fee 
mkt = new_market(liquidity_usd, quote, base, 0.003)
# create a cp swap execution engine
cp_amm = ConstantProductEngine(mkt)
# uni v2 lp strategy with arb to keep the price of the pool in line with mkt
amm_strategy=SimpleUniV2Strategy(cp_amm, arb_enabled=True)
# div protocol with buy back strategy on top the amm strat
prop_11487_strategy = DivProtocolStrategy(peg_price=0.02, strategy=amm_strategy)
# run simulation
simul = swap_simulation(df_trades, prop_11487_strategy)
# display results
show(new_div_simulation_figure(mkt, simul))

Function 'trade_summary' executed in 0.0075s
Function 'sim_results' executed in 0.0687s
Function 'swap_simulation' executed in 0.4336s


In [22]:
from bokeh.models import ColumnDataSource
from bokeh.palettes import Viridis3
from bokeh.plotting import figure, show

def plot_trade_summary(df):
    categories = df.index.tolist()
    transaction_types = df.columns.tolist()

    data = {'categories' : categories}
    for col in df.columns:
        data[col] = df[col].tolist()

    p = figure(y_range=categories, height=350, x_range=(-250000000, 250000000), 
               title="Trade Summary, by transaction type", toolbar_location=None)

    p.hbar_stack(transaction_types, y='categories', height=0.9, color=Viridis3, 
                 source=ColumnDataSource(data), legend_label=["%s" % x for x in transaction_types])

    p.y_range.range_padding = 0.1
    p.ygrid.grid_line_color = None
    p.legend.location = "top_left"
    p.axis.minor_tick_line_color = None
    p.outline_line_color = None

    show(p)

    
plot_trade_summary(mkt.assets())

In [24]:
from bokeh.models import ColumnDataSource
from bokeh.plotting import figure, show
from bokeh.transform import dodge

df = simul[""]

 df["volume_quote"]
source = ColumnDataSource(data=df["volume_quote"])

p = figure(x_range=fruits, y_range=(0, 10), title="Fruit Counts by Year",
           height=350, toolbar_location=None, tools="")

p.vbar(x=, top='2015', source=source, width=0.2, color="#c9d9d3", legend_label="2015")

p.x_range.range_padding = 0.1
p.xgrid.grid_line_color = None
p.legend.location = "top_left"
p.legend.orientation = "horizontal"

show(p)


In [38]:
from bokeh.plotting import figure, show

def plot_vbar(column):
    
    # Create a new figure
    p = figure(plot_height=350, title=column.name,
               toolbar_location=None, tools="")

    # Add vertical bars to the figure
    p.vbar(x=column.index.values.tolist(), top=column.values)

    # Display the figure
    show(p)


df = simul["breakdown"]

plot_vbar(df["volume_quote"])

In [40]:
from bokeh.models import ColumnDataSource
from bokeh.transform import factor_cmap
import pandas as pd

def plot_vbar(column):
    df['color'] = df[column.name].apply(lambda x: 'green' if x >= 0 else 'red')

    # Convert DataFrame to ColumnDataSource
    source = ColumnDataSource(df)

    # Create a new figure
    p = figure(plot_height=350, title=column.name, toolbar_location=None, tools="")

    # Add vertical bars to the figure
    p.vbar(x='trade_date', top=column.name, source=source, width=0.9,
           fill_color=factor_cmap('color', palette=['red', 'green'], factors=['red', 'green']))

    # Display the figure
    show(p)

# Test the function
# df = pd.DataFrame({'volume_quote': [-5, 10, -15, 20, -25]})
plot_vbar(df["volume_quote"])
